# COAL SUPPLY IN THE GERMAN EMPIRE DURING THE YEAR 1881

## Imports and global variables

In [1]:
%pylab inline
%load_ext autoreload
%autoreload 2

# Import libraries
import pandas as pd
import numpy as np

# Initiatize global variables
import settings as sgs
sgs.init()

# Import py functions of the project
from plot_cities import *
from network import *
from travels import *
from framer import *
from movie_maker import *

# Find path
import os
os.environ["PATH"] += os.pathsep + "."

# Hide warnings
import warnings
warnings.filterwarnings("ignore")

Populating the interactive namespace from numpy and matplotlib


## Code
### Load and pretreat data

In [2]:
# Read csv document which contains the data set in this precise format
df_cities = pd.read_csv(sgs._data_folder + r'cities.csv',delimiter=';')

# Fill null cells with zero and display the first columns of the dataset
df_cities.fillna(value=0,inplace=True)

# Display a sample of the dataframe
df_cities.head()

city_name  production  type_production  consumption   latitude  longitude
0     Aachen      2412.0              6.0        684.0  50.775000   6.084000
1  Altenburg      1362.0              9.0          0.0  50.991837  12.438535
2  Amsterdam         0.0              0.0        511.0  52.370216   4.895000
3   Annaberg         0.0              0.0          0.0  50.578560  13.004673
4      Arnau         0.0              0.0          0.0  50.539296  15.726031

In [3]:
len(df_cities)

205

In [4]:
# Read csv document which contains the data set in this precise format
df_routes = pd.read_csv(sgs._data_folder + r'routes.csv',delimiter=';')

# Fill null cells with zero and display the first columns of the dataset
df_routes.fillna(value=0,inplace=True)

# Display a sample of the dataframe
df_routes.head()

from_city    to_city  flux1  flux2  flux3   flux4  flux5  flux6  flux7  \
0  Wittenberge    Hamburg    0.0    0.0    0.0     0.0    0.0    0.0    0.0   
1        Düren     Aachen    0.0    0.0    0.0   937.0    0.0    0.0    0.0   
2      Viersen     Aachen    0.0    0.0    0.0  1536.0    0.0    0.0    0.0   
3      Zwickau  Altenburg    0.0    0.0    0.0     0.0    0.0  857.0    0.0   
4      Utrecht  Amsterdam    0.0    0.0    0.0   599.0    0.0    0.0    0.0   

   flux8   ...     fluxN1  fluxN2  fluxN3  fluxN4  fluxN5  fluxN6  fluxN7  \
0    0.0   ...        0.0     0.0     0.0     0.0     0.0     0.0     0.0   
1    0.0   ...        0.0     0.0     0.0     0.0     0.0     0.0     0.0   
2    0.0   ...        0.0     0.0     0.0     0.0     0.0     0.0     0.0   
3    0.0   ...        0.0     0.0     0.0     0.0     0.0     0.0     0.0   
4    0.0   ...        0.0     0.0     0.0     0.0     0.0     0.0     0.0   

   fluxN8  fluxN9  fluxN10  
0     0.0     0.0     51.0  
1     0.0     0.0      0.0  
2     0.0     0.0      0.0  
3     0.0     0.0      0.0  
4     0.0     0.0      0.0  

[5 rows x 22 columns]

In [5]:
len(df_routes)

347

In [6]:
# Aggregate data about city coordinates, which are found in the prod_conso.csv data folder with the 
# data about trade routes

df_cities_coordinates = df_cities[['city_name','latitude','longitude']]
df_cities_coordinates = df_cities_coordinates.rename(columns = {'city_name':'from_city'})
df_flux = pd.merge(df_cities_coordinates, df_routes, on='from_city')
df_cities_coordinates = df_cities_coordinates.rename(columns = {'from_city':'to_city'})
df_flux = pd.merge(df_cities_coordinates, df_flux,on='to_city')

df_flux = df_flux.rename(columns = {'latitude_x':'to_latitude',
                                    'latitude_y':'from_latitude',
                                    'longitude_x':'to_longitude',
                                    'longitude_y':'from_longitude'})

# Sum all the different flux to get the total flux
df_flux['flux'] = df_flux.flux1
for ind_, row in df_flux.iterrows():
    df_flux.set_value(ind_,'flux', sum(row[6:-1]))
    
# Display a sample of the dataframe
df_flux.sort_values(by = ['flux'], ascending = False, inplace = True)
df_flux.tail()

to_city  to_latitude  to_longitude    from_city  from_latitude  \
65       Dessau    51.832500     12.234099       Cöthen      51.744505   
162     Kolberg    54.181679     15.569580       Ostsee      55.517436   
141       Husum    54.485378      9.053620      Nordsee      55.392840   
240  Neumünster    54.074100      9.984670     Schlewig      54.514960   
343    Wurzburg    49.794260      9.927490  Schweinfurt      50.049099   

     from_longitude  flux1  flux2  flux3  flux4  ...   fluxN2  fluxN3  fluxN4  \
65        11.971218    0.0    0.0    0.0    0.0  ...      0.0     0.0     0.0   
162       15.945026    0.0    0.0    0.0    0.0  ...      0.0     0.0     0.0   
141        4.392499    0.0    0.0    0.0    0.0  ...      0.0     0.0     0.0   
240        9.566770    0.0    0.0    0.0    0.0  ...      0.0     0.0     0.0   
343       10.231160    0.0    0.0    0.0    0.0  ...      0.0     0.0     0.0   

     fluxN5  fluxN6  fluxN7  fluxN8  fluxN9  fluxN10  flux  
65      0.0     0.0     0.0     0.0     0.0      0.0   8.0  
162     0.0     0.0     0.0     8.0     0.0      0.0   8.0  
141     0.0     0.0     0.0     7.0     0.0      0.0   7.0  
240     0.0     0.0     0.0     0.0     0.0      0.0   6.0  
343     0.0     0.0     0.0     0.0     0.0      0.0   5.0  

[5 rows x 27 columns]

In [7]:
len(df_flux)

347

In [8]:
# Aggregate data about city coordinates, which are found in the prod_conso.csv data folder with the 
# data about trade routes

df_cities_coordinates = df_cities[['city_name','latitude','longitude']]
df_cities_coordinates = df_cities_coordinates.rename(columns = {'city_name':'from_city'})
df_flux = pd.merge(df_cities_coordinates, df_routes, on='from_city')
df_cities_coordinates = df_cities_coordinates.rename(columns = {'from_city':'to_city'})
df_flux = pd.merge(df_cities_coordinates, df_flux, on='to_city')

df_flux = df_flux.rename(columns = {'latitude_x':'to_latitude',
                                    'latitude_y':'from_latitude',
                                    'longitude_x':'to_longitude',
                                    'longitude_y':'from_longitude'})

# Sum all the different flux to get the total flux
df_flux['flux'] = df_flux.flux1
for ind_, row in df_flux.iterrows():
    df_flux.set_value(ind_,'flux', sum(row[6:-1]))
    
# Display a sample of the dataframe
df_flux.head()

to_city  to_latitude  to_longitude from_city  from_latitude  \
0     Aachen    50.775000      6.084000     Düren      50.799850   
1     Aachen    50.775000      6.084000   Viersen      51.255700   
2  Altenburg    50.991837     12.438535   Zwickau      50.718319   
3  Amsterdam    52.370216      4.895000   Utrecht      52.090736   
4   Annaberg    50.578560     13.004673  Chemnitz      50.827847   

   from_longitude  flux1  flux2  flux3   flux4   ...    fluxN2  fluxN3  \
0        6.486960    0.0    0.0    0.0   937.0   ...       0.0     0.0   
1        6.398340    0.0    0.0    0.0  1536.0   ...       0.0     0.0   
2       12.494156    0.0    0.0    0.0     0.0   ...       0.0     0.0   
3        5.121420    0.0    0.0    0.0   599.0   ...       0.0     0.0   
4       12.921370    0.0    0.0    0.0     0.0   ...       0.0     0.0   

   fluxN4  fluxN5  fluxN6  fluxN7  fluxN8  fluxN9  fluxN10    flux  
0     0.0     0.0     0.0     0.0     0.0     0.0      0.0   937.0  
1     0.0     0.0     0.0     0.0     0.0     0.0      0.0  1536.0  
2     0.0     0.0     0.0     0.0     0.0     0.0      0.0   857.0  
3     0.0     0.0     0.0     0.0     0.0     0.0      0.0   599.0  
4     0.0     0.0     0.0     0.0     0.0     0.0      0.0    74.0  

[5 rows x 27 columns]

In [9]:
if len(df_flux) != len(df_routes):
    raise Exception('Error : missing rows in the cities.csv folder. Some cities found in ' +
                    'routes.csv are not documented.')

### Create interactive maps in order to present data
First, we will create interactive maps directly concerning cities: their production, their consumption, as well as net import-export.
#### Production

In [10]:
production_map = plot_cities(df_cities,'production')
production_map

In [11]:
production_map.save(sgs._html_folder + "production.html")

#### Production by production type

In [12]:
production_map_col = plot_cities_production(df_cities)
production_map_col

In [13]:
production_map_col.save(sgs._html_folder + "production_col.html")

#### Consumption

In [14]:
consumption_map = plot_cities(df_cities,"consumption")
consumption_map

In [15]:
consumption_map.save(sgs._html_folder + "consumption.html")

#### Net import/export

In [16]:
import_export_map = plot_cities_import_export(df_cities)
import_export_map

In [17]:
import_export_map.save(sgs._html_folder + "import_export.html")

Now, we will focus on the fluid dimension and display information that is more directly related to the transport of coal. This interactive display should allow us to visualize the main transportation sites.

To this end, we will calculate the quantities of coal arriving and departing from each city, as well as the total transit.

In [18]:
# Empty lists
cities_list, arriving_list, departing_list = [], [], []

# Append each city to the cities_list and sum the total quantities of arriving and departing goods
for ind, city in enumerate(df_cities.city_name):
    cities_list.append(city)
    df_arriving = df_flux[df_flux.to_city == city]
    arriving_list.append(sum(df_arriving.flux))
    df_departing = df_flux[df_flux.from_city == city]
    departing_list.append(sum(df_departing.flux))

# Transfer the filled list into a dictionary element    
dict_ = {
    'city_name' : cities_list,
    'arriving_flux' : arriving_list,
    'departing_flux' : departing_list
}

# Create a new dataframe from this dictionary
df_transit = pd.DataFrame.from_dict(dict_)

# Total transit is defined as total arriving coal + total departing coal
df_transit['transiting_flux'] = df_transit['arriving_flux'] + df_transit['departing_flux']

# Append informations about cities coordinates in this dataframe
df_cities_coordinates = df_cities[['city_name','latitude','longitude']]
df_transit = pd.merge(df_cities_coordinates,df_transit,on='city_name')
df_transit.head()

city_name   latitude  longitude  arriving_flux  departing_flux  \
0     Aachen  50.775000   6.084000         2473.0          3340.0   
1  Altenburg  50.991837  12.438535          857.0          1599.0   
2  Amsterdam  52.370216   4.895000          599.0             0.0   
3   Annaberg  50.578560  13.004673           74.0             0.0   
4      Arnau  50.539296  15.726031          656.0             0.0   

   transiting_flux  
0           5813.0  
1           2456.0  
2            599.0  
3             74.0  
4            656.0

#### Arriving coal

In [19]:
arriving_map = plot_cities(df_transit,"arriving_flux")
arriving_map

In [20]:
arriving_map.save(sgs._html_folder + "arriving_map.html")

#### Departing coal

In [21]:
departing_map = plot_cities(df_transit,"departing_flux")
departing_map

In [22]:
departing_map.save(sgs._html_folder + "departing_map.html")

#### Total transiting coal

In [23]:
transiting_map = plot_cities_transiting_flux(df_transit)
transiting_map

In [24]:
transiting_map.save(sgs._html_folder + "transiting_map.html")

### Static network visualisation
We will now visualize the trade routes between cities, in a simple static form. We will present two options for this representation. The first version will be gold and the second version will propose a colour variation for sea/river routes (blue), land routes (gold) and mixed routes (green).

In [25]:
# Define boundaries of the map
max_lon, min_lon = df_cities["longitude"].max(), df_cities["longitude"].min()
min_lat, max_lat = df_cities["latitude"].min(), df_cities["latitude"].max()

In [26]:
df_flux.head()

to_city  to_latitude  to_longitude from_city  from_latitude  \
0     Aachen    50.775000      6.084000     Düren      50.799850   
1     Aachen    50.775000      6.084000   Viersen      51.255700   
2  Altenburg    50.991837     12.438535   Zwickau      50.718319   
3  Amsterdam    52.370216      4.895000   Utrecht      52.090736   
4   Annaberg    50.578560     13.004673  Chemnitz      50.827847   

   from_longitude  flux1  flux2  flux3   flux4   ...    fluxN2  fluxN3  \
0        6.486960    0.0    0.0    0.0   937.0   ...       0.0     0.0   
1        6.398340    0.0    0.0    0.0  1536.0   ...       0.0     0.0   
2       12.494156    0.0    0.0    0.0     0.0   ...       0.0     0.0   
3        5.121420    0.0    0.0    0.0   599.0   ...       0.0     0.0   
4       12.921370    0.0    0.0    0.0     0.0   ...       0.0     0.0   

   fluxN4  fluxN5  fluxN6  fluxN7  fluxN8  fluxN9  fluxN10    flux  
0     0.0     0.0     0.0     0.0     0.0     0.0      0.0   937.0  
1     0.0     0.0     0.0     0.0     0.0     0.0      0.0  1536.0  
2     0.0     0.0     0.0     0.0     0.0     0.0      0.0   857.0  
3     0.0     0.0     0.0     0.0     0.0     0.0      0.0   599.0  
4     0.0     0.0     0.0     0.0     0.0     0.0      0.0    74.0  

[5 rows x 27 columns]

#### Simple unicolor visualisation

In [27]:
folium_map = get_beautiful_base_image_map(df_flux)
folium_map

In [28]:
folium_map.save(sgs._html_folder + "coal_supply.html")

#### Visualisation including color variation for naval routes

In [29]:
folium_map = get_beautiful_tricolor_base_image_map(df_flux)
folium_map

In [30]:
folium_map.save(sgs._html_folder + "coal_supply_tricolor.html")

#### Visualisation of land routes only

In [31]:
folium_map = get_beautiful_base_image_map_by_route_category(df_flux, mode = 'land')
folium_map

In [32]:
folium_map.save(sgs._html_folder + "coal_supply_land.html")

In [33]:
folium_map = get_beautiful_base_image_map_by_route_category(df_flux, mode = 'naval')
folium_map

In [34]:
folium_map.save(sgs._html_folder + "coal_supply_naval.html")

### Simulation
We will now try to simulate a more dynamic version of these trade routes. To do this, we will simulate a train and transport boat schedule over an entire year of 1881, with a scale of 5 minutes. These artificial trains and boats will move on the map at a realistic historical rate (taking into account the capacity of the transport trains of the time and the quantity of coal to be transported), in the form of small points (trains) or triangles (boats).

In [35]:
# Creation of the "artificial timetable"
df_trains = create_timetable(df_flux).sort_values('departure_time')
df_trains.head()

from_city     to_city departure_time        arrival_time  coal_type  \
24162         Köln        Bonn     1881-01-01 1881-01-01 00:25:00          4   
305843    Neustadt  Strassburg     1881-01-01 1881-01-01 01:30:00          9   
320543  Düsseldorf     Viersen     1881-01-01 1881-01-01 00:40:00          4   
173709     Viersen        Köln     1881-01-01 1881-01-01 01:05:00          4   
197520  Maastricht       Liège     1881-01-01 1881-01-01 00:25:00          4   

        is_naval  
24162          0  
305843         0  
320543         0  
173709         0  
197520         0

In [36]:
# Add information about cities coordinates
df_cities_coordinates = df_cities[['city_name','latitude','longitude']]
df_cities_coordinates = df_cities_coordinates.rename(columns = {'city_name':'from_city'})
df_trips = pd.merge(df_cities_coordinates,df_trains,on='from_city')
df_cities_coordinates = df_cities_coordinates.rename(columns = {'from_city':'to_city'})
df_trips = pd.merge(df_cities_coordinates,df_trips,on='to_city')

# Rename columns with appropriate names
df_trips = df_trips.rename(columns = {'latitude_x':'to_latitude',
                                    'latitude_y':'from_latitude',
                                    'longitude_x':'to_longitude',
                                    'longitude_y':'from_longitude'})

# Sort in a chronological order
df_trips = df_trips.sort_values("departure_time",ascending=True)

# Convert in a datatime format
df_trips["departure_time"] = pd.to_datetime(df_trips["departure_time"])
df_trips["arrival_time"] = pd.to_datetime(df_trips["arrival_time"])

# Display the first columns
df_trips.head()

to_city  to_latitude  to_longitude   from_city  from_latitude  \
173357        Köln    50.940529      6.959910     Viersen      51.255700   
305788  Strassburg    48.582951      7.743750    Neustadt      49.350185   
197460       Liège    50.643910      5.571560  Maastricht      50.851368   
152082      Kassel    51.312710      9.479746     Warburg      51.485130   
320097     Viersen    51.255700      6.398340  Düsseldorf      51.224960   

        from_longitude departure_time        arrival_time  coal_type  is_naval  
173357        6.398340     1881-01-01 1881-01-01 01:05:00          4         0  
305788        8.148689     1881-01-01 1881-01-01 01:30:00          9         0  
197460        5.690972     1881-01-01 1881-01-01 00:25:00          4         0  
152082        9.147030     1881-01-01 1881-01-01 00:40:00          4         0  
320097        6.775670     1881-01-01 1881-01-01 00:40:00          4         0

In [37]:
print(len(df_trips))

334939


#### Time capture of the simulation on the 7th of January 1881, at 21:30

In [38]:
folium_map = get_image_map(pd.to_datetime('1881-01-07 21:30:00'), df_trips, df_flux)
folium_map

#### Create frames for each time slot of the simulation
NB : this can take a lot of time, the frames already created are stored in the "png" folder. Here under you can follow the progress of the creation process.

In [ ]:
coach(df_trips, df_flux, 0, 6048)

#### Convert the frames into a movie

In [ ]:
movie_maker(0, 6048)